# Examples

This Jupyter notebook shows some examples for the different functions of the Julia module `zaf`.

Functions:
- `stft` - [Short-time Fourier transform (STFT)](#stft)
- `istft` - [Inverse STFT](#istft)
- `cqtkernel` - [Constant-Q transform (CQT) kernel](#cqtkernel)
- `cqtspectrogram` - [CQT spectrogram using a CQT kernel](#cqtspectrogram)
- `cqtchromagram` - [CQT chromagram using a CQT kernel](#cqtchromagram)
- `mfcc` - [Mel frequency cepstrum coefficients (MFCCs)](#mfcc)
- `dct` - [Discrete cosine transform (DCT) using the fast Fourier transform (FFT)](#dct)
- `dst` - [Discrete sine transform (DST) using the FFT](#dst)
- `mdct` - [Modified discrete cosine transform (MDCT) using the FFT](#mdct)
- `imdct` - [Inverse MDCT using the FFT](#imdct)

Other:
- `wavread` - Read a WAVE file (using Scipy)
- `wavwrite` - Write a WAVE file (using SciPy)
- `sigplot` - Plot an audio signal in seconds
- `specshow` - Display an audio spectrogram in dB, seconds, and Hz
- `cqtspecshow` - Display a CQT audio spectrogram in dB, seconds, and Hz
- `cqtchromshow` - Display a CQT audio chromagram in seconds and chroma


Author:
- Zafar Rafii
- zafarrafii@gmail.com
- http://zafarrafii.com
- https://github.com/zafarrafii
- https://www.linkedin.com/in/zafarrafii/
- 11/10/20

## <a id="stft"></a>Short-time Fourier transform (STFT)

```
audio_stft = zaf.stft(audio_signal, window_function, step_length)

Inputs:
    audio_signal: audio signal (number_samples,)
    window_function: window function (window_length,)
    step_length: step length in samples
Output:
    audio_stft: audio STFT (window_length, number_frames)
```

### Example: compute and display the spectrogram from an audio file

In [17]:
# Load the modules
include("./zaf.jl")
using .zaf
using WAV
using Statistics
using Plots

# Read the audio signal (normalized) with its sampling frequency in Hz, and average it over its channels
audio_signal, sampling_frequency = wavread("audio_file.wav");
audio_signal = mean(audio_signal, dims=2);

# Set the window duration in seconds (audio is stationary around 40 milliseconds)
window_duration = 0.04;

# Derive the window length in samples (use powers of 2 for faster FFT and constant overlap-add (COLA))
window_length = nextpow(2, ceil(Int, window_duration*sampling_frequency));

# Compute the window function (periodic Hamming window for COLA)
window_function = zaf.hamming(window_length, "periodic");

# Set the step length in samples (half of the window length for COLA)
step_length = convert(Int, window_length/2);

# Compute the STFT
audio_stft = zaf.stft(audio_signal, window_function, step_length)

# Derive the magnitude spectrogram (without the DC component and the mirrored frequencies)
audio_spectrogram = abs.(audio_stft[2:convert(Int, window_length/2)+1, :])

# Magnitude spectrogram (without the DC component and the mirrored frequencies)
audio_spectrogram = abs.(audio_stft[2:convert(Int64, window_length/2)+1,:]);

In [26]:
# Display the spectrogram in dB, seconds, and Hz
#plt = heatmap(20*log10.(audio_spectrogram), size=(1000, 500), c=cgrad([:blue,:yellow,:red]))

plt = heatmap(20*log10.(audio_spectrogram), size=(1000, 500), fillcolor=:jet)
display(plt)
# x_labels = [string(round(i*step_length/sample_rate, 2)) for i = 1:size(audio_spectrogram, 2)];
# y_labels = [string(round(i*sample_rate/window_length/1000, 2)) for i = 1:size(audio_spectrogram, 1)];
# heatmap(x_labels, y_labels, 20*log10.(audio_spectrogram))